# Create Video!

In [ ]:
pip install opencv-python opencv-python-headless  # If you do not need GUI features


## Creating the demo


In [1]:
import os
import subprocess
import logging
from glob import glob

# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

def create_h265_video(input_folder, output_file, fps=30, frames_per_image=3):
    if not os.path.exists(input_folder):
        logger.error(f"Input folder '{input_folder}' does not exist.")
        return

    png_files = sorted(glob(os.path.join(input_folder, '*.png')))
    if not png_files:
        logger.error(f"No PNG files found in {input_folder}")
        return

    num_images = len(png_files)
    logger.info(f"Found {num_images} PNG files.")

    # Calculate expected duration
    expected_duration = (num_images * frames_per_image) / fps
    logger.info(f"Expected duration: {expected_duration:.2f} seconds")

    # Create a temporary file list
    with open('temp_file_list.txt', 'w') as f:
        for file in png_files:
            f.write(f"file '{file}'\n")
            f.write(f"duration {frames_per_image/fps:.6f}\n")

    # FFmpeg command to create video
    ffmpeg_command = [
        'ffmpeg',
        '-f', 'concat',
        '-safe', '0',
        '-i', 'temp_file_list.txt',
        '-vsync', 'vfr',
        '-pix_fmt', 'yuv420p',  # Ensure compatible color space
        '-color_range', '1',    # Ensure full color range
        '-color_primaries', '1',
        '-color_trc', '1',
        '-colorspace', '1',
        '-c:v', 'libx265',
        '-crf', '23',
        '-preset', 'medium',
        '-tag:v', 'hvc1',
        '-y',
        output_file
    ]

    try:
        logger.info("Starting video creation...")
        result = subprocess.run(ffmpeg_command, check=True, capture_output=True, text=True)
        logger.info(f"FFmpeg output:\n{result.stdout}")
        
        if os.path.exists(output_file):
            logger.info(f"Video created successfully: {output_file}")
            
            # Verify the output
            probe_command = ['ffprobe', '-v', 'error', '-show_entries', 'stream=codec_name,width,height,duration', '-of', 'default=noprint_wrappers=1', output_file]
            probe_result = subprocess.run(probe_command, capture_output=True, text=True)
            logger.info(f"Video properties:\n{probe_result.stdout}")
            
            # Check if the video is playable and has correct duration
            play_check_command = ['ffprobe', '-v', 'error', '-show_entries', 'format=duration', '-of', 'default=noprint_wrappers=1:nokey=1', output_file]
            try:
                duration_result = subprocess.run(play_check_command, check=True, capture_output=True, text=True)
                actual_duration = float(duration_result.stdout.strip())
                logger.info(f"Actual video duration: {actual_duration:.2f} seconds")
                if abs(actual_duration - expected_duration) > 1:  # Allow 1 second tolerance
                    logger.warning(f"Video duration mismatch. Expected: {expected_duration:.2f}, Actual: {actual_duration:.2f}")
                else:
                    logger.info("Video duration check passed.")
            except subprocess.CalledProcessError:
                logger.error("Video duration check failed.")
        else:
            logger.error(f"Output file was not created: {output_file}")
    
    except subprocess.CalledProcessError as e:
        logger.error(f"Error during video creation: {e}")
        logger.error(f"FFmpeg error output:\n{e.stderr}")
    
    finally:
        # Clean up
        if os.path.exists('temp_file_list.txt'):
            os.remove('temp_file_list.txt')

if __name__ == "__main__":
    input_folder = 'train'
    output_file = 'output_production.mp4'
    fps = 30
    frames_per_image = 3

    create_h265_video(input_folder, output_file, fps, frames_per_image)









2024-08-05 19:36:09,033 - INFO - Found 911 PNG files.
2024-08-05 19:36:09,035 - INFO - Starting video creation...
2024-08-05 19:36:24,399 - INFO - FFmpeg output:

2024-08-05 19:36:24,400 - INFO - Video created successfully: output_production.mp4
2024-08-05 19:36:24,483 - INFO - Video properties:
codec_name=hevc
width=1024
height=1024
duration=0.160000

2024-08-05 19:36:25,344 - INFO - Video playback check passed.
